# Loading and Visualizing the Netflix dataset

In [1]:
import pandas as pd
import numpy as np

from plotly import tools
import plotly.offline as py
import plotly.graph_objs as go

py.init_notebook_mode(connected=True)

### Loading the data

Let's start this by trying to load the dataset provided by Kaggle. On the description of the dataset (available [here](https://www.kaggle.com/netflix-inc/netflix-prize-data/version/1)), we learn that the rating data is split between four files named `combined_data_{1, 2, 3, 4}.txt`, each of them formatted in the following way:

```
MovieId1:                  -- Header   \ 
UserId11,Rating11,Date11   \            | Movie Block
UserId12,Rating12,Date12    | Ratings   |
...                        /           /
MovieId2:
UserId21,Rating21,Date21
UserId22,Rating22,Date22
...
```

As you can see, this is not a simple CSV. We will need to transform this file into a datasets suitable for analysis.

In [2]:
# Let's start by loading the four parts of the dataset into a single dataframe
headers = ['user_id','rating','date']
df = pd.read_csv('../dataset/combined_data_1.txt', names=headers)

df_part = pd.read_csv('../dataset/combined_data_2.txt', names=headers)
df = df.append(df_part, ignore_index=True)

df_part = pd.read_csv('../dataset/combined_data_3.txt', names=headers)
df = df.append(df_part, ignore_index=True)

df_part = pd.read_csv('../dataset/combined_data_4.txt', names=headers)
df = df.append(df_part, ignore_index=True)

print('Found {} rows in the Netflix dataset.'.format(len(df)))

Found 100498277 rows in the Netflix dataset.


Alright, we now have a large dataset (over 100M rows!) containing all of our ratings, together with each of the header rows containing the movie identifier of each ratings block.

Our goal will be to remove the header rows from our dataset and instead add a `movie_id` column to our dataset to match each rating to the movie being rated.

In [3]:
# We can start by finding the header rows present in the dataset. An example of such a row can
# be found at the very beginning of the dataset,].
df.iloc[0]

user_id     1:
rating     NaN
date       NaN
Name: 0, dtype: object

In [4]:
# We can thus find each header row by selecting rows from our dataframe with a NaN rating.
header_rows = df[df['rating'].isna()]
print('The Netflix dataset contains {} movies'.format(len(header_rows)))

The Netflix dataset contains 17770 movies


In [7]:
# Alright, we can now use the indices of the header rows to match ratings to their movies.

# Start by initializing the movie_id column of the dataframe.
df['movie_id'] = np.nan

num_movies = len(header_rows)
for i in range(num_movies - 1):
    # Extract the movie id, removing the trailing ':' and parsing it as a number
    movie_id = int(header_rows['user_id'].iloc[i][:-1])
    
    # Compute the index range for the ratings of this block
    block_from = header_rows.index[i] + 1
    block_to = header_rows.index[i+1]
    
    # Assign the movie id to the ratings in the block
    df['movie_id'].loc[block_from:block_to] = movie_id
    
# Finally, we can filter out the header rows from our dataset
df = df[~df['rating'].isna()]

### Exploratory data analysis

Now that the data is loaded, we are ready to explore our data and hopefully gain some insights.

In [83]:
df_by_user = df.groupby('user_id').count()
data = [go.Histogram(x=df_by_user['rating'])]
py.iplot(data)

In [12]:
df_by_rating = df.groupby('rating').count()
data = [go.Bar(x=df_by_rating.index, y=df_by_rating['user_id'])]
py.iplot(data)